In [2]:
import os
import random
import requests
import numpy as np

from gensim.models import KeyedVectors
import logging

from gensim import utils
import nltk

import networkx as nx
import matplotlib.pyplot as plt

import shutil
import smart_open
from sys import platform
import random
import tensorflow as tf
import json
model = KeyedVectors.load_word2vec_format(os.path.join( 'Compute metrics/glove_2.2M.txt'))

In [3]:
_is_relevant = [.0, 1.]
_is_not_relevant = [1., 0.]

_logger = logging.getLogger(__name__)


def get_words(text):
    tokenizer = nltk.tokenize.TweetTokenizer()
    words = tokenizer.tokenize(utils.to_unicode(text))
    return words


def capitalize(word):
    return word[0].upper() + word[1:]


def low_case(word):
    return word[0].lower() + word[1:]


def infer_vector_from_word(model, word):
    vector = np.zeros(300)
    try:
        vector = model[word]
    except:
        try:
            vector = model[capitalize(word)]
        except:
            try:
                vector = model[low_case(word)]
            except:
                pass
    return vector


def infer_vector_from_doc(model, text):
    words = get_words(text)
    vector = np.zeros(300)
    for word in words:
        vector += infer_vector_from_word(model, word)
    norm = np.linalg.norm(vector)
    if norm > 0:
        vector /= norm
    return vector


def get_vectors_from_nodes_in_graph(g, model):
    nodes = nx.nodes(g)
    vectors = []
    for node in nodes:
        text = node.replace('_', ' ')
        text = text.split('|')[0]
        vectors.append(infer_vector_from_doc(model, text))
    return np.array(vectors)


def get_types_from_nodes_in_graph(g):
    nodes = nx.nodes(g)
    vectors = []
    for node in nodes:
        texts = node.split('|')
        vector = np.zeros(3)
        if 'NODE' in texts:
            vector[0] = 1.
        if 'EDGE' in texts:
            vector[1] = 1.
        vectors.append(vector)
    return np.array(vectors)


def get_edge_name_with_signature(node_str):
    node_str = node_str.split('|')[0].lower()
    node_str += '|EDGE'
    return node_str


def get_node_name_with_signature(node_str):
    node_str = node_str.split('|')[0].lower()
    node_str += '|NODE'
    return node_str


def add_triplets_to_graph_bw(g, triplets):
    for n1, r, n2 in triplets:
        clean_n1 = get_node_name_with_signature(n1)
        clean_n2 = get_node_name_with_signature(n2)
        clean_r = get_edge_name_with_signature(r)
        g.add_node(clean_n1)
        g.add_node(clean_n2)
        g.add_node(clean_r)
        g.add_edge(clean_n2, clean_r, **{'label': 'to_relation'})
        g.add_edge(clean_r, clean_n1, **{'label': 'to_node'})
    return g


def plot_graph(g):
    layout = nx.shell_layout(g)
    nx.draw_networkx(g, pos=layout)
    nx.draw_networkx_edge_labels(g, pos=layout)
    plt.show()


def get_chunks(l, n):
    return [l[i:i + n] for i in range(0, len(l), n)]


def bin_data_into_buckets(data, batch_size):
    buckets = []
    size_to_data_dict = {}
    for item in data:
        seq_length = len(item['graph']['vectors'])
        question_length = len(item['question_vectors'])
        try:
            size_to_data_dict[(seq_length, question_length)].append(item)
        except:
            size_to_data_dict[(seq_length, question_length)] = [item]
    for key in size_to_data_dict.keys():
        data = size_to_data_dict[key]
        chunks = get_chunks(data, batch_size)
        for chunk in chunks:
            buckets.append(chunk)
    return buckets





In [4]:
def translate_from_url(url):
    if '/' in url and '-' not in url:

        item = url.split('/')[-1]
#             print('from wikidata items_1: {}'.format(item))
    elif '/' in url and '-' in url:
        item = url.split('/')[-1].split('-')[0]
#             print('from wikidata items_2: {}'.format(item))
    else:
        item = url
#             print('from wikidata items_3: {}'.format(item))
    return item

def reverse_lookup(word):
    return reverse_dict[word.lower()]


In [5]:
def get_wikidata_id_from_wikipedia_id(wikipedia_id):
    url = 'https://en.wikipedia.org/w/api.php?action=query&prop=pageprops&pageids=%s&format=json' % str(
        wikipedia_id)
    try:
        return requests.get(url).json()['query']['pages'][str(wikipedia_id)]['pageprops']['wikibase_item']
    except:
        return ''


def convert_text_into_vector_sequence(model, text):
    words = get_words(text)
    vectors = []
    for word in words:
        vectors.append(infer_vector_from_word(model, word))
    return vectors


def get_item_mask_for_words(text, item):
    words = get_words(text)
    types = []
    words_in_item = get_words(item.lower())
    for word in words:
        types.append([1. if word.lower() in words_in_item else 0.] * 200)
    return types




def infer_vector_from_vector_nodes(vector_list):
    vector = np.zeros(300)
    for v in vector_list:
        vector += v
    norm = np.linalg.norm(vector)
    if norm > 0:
        vector /= norm
    return vector


def create_text_item_graph_dict(text, item, wikidata_id):
    text_item_graph_dict = {}
    text_item_graph_dict['text'] = text
    text_item_graph_dict['item'] = item
    text_item_graph_dict['wikidata_id'] = wikidata_id
    text_item_graph_dict['graph'] = get_graph_from_wikidata_id(wikidata_id, item)
    # text_item_graph_dict['item_vector'] = infer_vector_from_doc(_model, item)
    text_item_graph_dict['item_vector'] = infer_vector_from_vector_nodes(text_item_graph_dict['graph']['vectors'])
    text_item_graph_dict['question_vectors'] = convert_text_into_vector_sequence(model, text)
    text_item_graph_dict['question_mask'] = get_item_mask_for_words(text, item)
    return text_item_graph_dict



def get_json_data(json_data, count):
    data = []
    lost=[]
    for  json_item in json_data[:count]:
       
        try:
            text = json_item['text']
            item = json_item['string']

            wikidata_id = json_item['correct_id']
#             print('before problem {}'.format(i))
            text_item_graph_dict = create_text_item_graph_dict(text, item, wikidata_id)
#             print('before problem if not with graph {}'.format(i))
            text_item_graph_dict['answer'] = _is_relevant
#             print('before problem if not with answer {}'.format(i))
            data.append(text_item_graph_dict)

            wikidata_id = json_item['wrong_id']
            text_item_graph_dict = create_text_item_graph_dict(text, item, wikidata_id)
            text_item_graph_dict['answer'] = _is_not_relevant
            

            data.append(text_item_graph_dict)
        except Exception as e:
#             print(str(e))
            lost.append(json_item)
    return data, lost



def get_graph_from_wikidata_id(wikidata_id, central_item):
    url = 'https://query.wikidata.org/bigdata/namespace/wdq/sparql'
    data = requests.get(url, params={'query': _query % wikidata_id,
                                     'format': 'json'}).json()
    triplets = []
    for item in data['results']['bindings']:
        try:
            from_item = translate_from_url(wikidata_id)
            relation = translate_from_url(item['rel']['value'])
            to_item = translate_from_url(item['item']['value'])
            triplets.append((from_item, relation, to_item))
        except:
            pass
        try:
            from_item = translate_from_url(item['item']['value'])
            relation = translate_from_url(item['rel2']['value'])
            to_item = translate_from_url(item['to_item']['value'])
            triplets.append((from_item, relation, to_item))
        except:
            pass
    triplets = sorted(list(set(triplets)))
    if not triplets:
        raise RuntimeError("This graph contains no suitable triplets.")
    return get_adjacency_matrices_and_vectors_given_triplets(triplets, central_item, model)

In [6]:
def get_bw_graph(triplets):
    g_bw = nx.DiGraph()
    add_triplets_to_graph_bw(g_bw, triplets)
    return g_bw


def get_adjacency_matrices_and_vectors_given_triplets(triplets, central_item, model):
    g_bw = get_bw_graph(triplets)

    vectors = get_vectors_from_nodes_in_graph(g_bw, model)
    node_types = get_types_from_nodes_in_graph(g_bw)
    nodelist = list(g_bw.nodes())
    try:
        central_node_index = nodelist.index(central_item + '|NODE')
        nodelist[central_node_index], nodelist[0] = nodelist[0], nodelist[central_node_index]
    except Exception as e:
        print('nodelist:', e)
        raise e
    A_bw = np.array(nx.to_numpy_matrix(g_bw, nodelist=nodelist))
    return {'A_bw': A_bw,
            'vectors': vectors,
            'types': node_types}



In [107]:
_query = '''
SELECT ?rel ?item ?rel2 ?to_item {
  wd:%s ?rel ?item
  OPTIONAL { ?item ?rel2 ?to_item }
  FILTER regex (str(?item), '^((?!statement).)*$') .
  FILTER regex (str(?item), '^((?!https).)*$') .
} LIMIT 400
'''


In [11]:
def compute_new_adjacency_matrix(embedding_size, attention_size, memory_dim, A, H, question_vector, name):
    Wa = tf.Variable(tf.compat.v1.random_uniform([embedding_size + memory_dim, attention_size], -_rw, _rw),
                     name='Wa_' + name)
    ba = tf.Variable(tf.compat.v1.random_uniform([attention_size], -_rw, _rw), name='b0_fw' + name)
    #problem with tf.nn
    WHQ_projection = lambda x: tf.nn.relu(tf.matmul(tf.concat([x, question_vector], axis=1), Wa) + ba)
    WHQ = tf.map_fn(WHQ_projection, H)
    WHQ = tf.transpose(WHQ, perm=[1, 0, 2])
    #problem with tf.nn
    WHQ_squared_projection = lambda x: tf.nn.softmax(tf.matmul(x, tf.transpose(x, perm=[1, 0])))
    WHQ_squared = tf.map_fn(WHQ_squared_projection, WHQ)
    new_A = tf.multiply(A, WHQ_squared)
    return new_A


def GCN_layer_fw(embedding_size, hidden_layer1_size, memory_dim, hidden, Atilde_fw, question_vector, name):
    new_A = compute_new_adjacency_matrix(embedding_size, 250, memory_dim, Atilde_fw, hidden, question_vector, name)
    W0_fw = tf.Variable(tf.compat.v1.random_uniform([embedding_size, hidden_layer1_size], -_rw, _rw),
                        name='W0_fw' + name)
    b0_fw = tf.Variable(tf.compat.v1.random_uniform([hidden_layer1_size], -_rw, _rw), name='b0_fw' + name)
    left_X1_projection_fw = lambda x: tf.matmul(x, W0_fw) + b0_fw
    left_X1_fw = tf.map_fn(left_X1_projection_fw, hidden)
    left_X1_fw = tf.transpose(left_X1_fw, perm=[1, 0, 2], name='left_X1_fw' + name)
    #problem with tf.nn
    X1_fw = tf.nn.relu(tf.matmul(new_A, left_X1_fw))
    X1_fw = tf.transpose(X1_fw, perm=[1, 0, 2])
    return X1_fw

In [12]:
TINY = 1e-6
ONE = tf.constant(1.)
NAMESPACE = 'gcn_qa'
forbidden_weight = 1.
_weight_for_positive_matches = 1.
_rw = 1e-1
tf.compat.v1.disable_eager_execution()
class GCN_QA(object):
    _nodes_vocab_size = 300
    _question_vocab_size = 300
    _question_vector_size = 150
    _types_size = 3
    _mask_size = 200
    _types_proj_size = 5
    _word_proj_size = 50
    _word_proj_size_for_rnn = 50
    _word_proj_size_for_item = 50
    _internal_proj_size = 250
    _hidden_layer1_size = 250
    _hidden_layer2_size = 250
    _output_size = 2

    _memory_dim = 100
    _stack_dimension = 2

    def __init__(self, dropout=1.0):
        tf.compat.v1.reset_default_graph()
        with tf.compat.v1.variable_scope(NAMESPACE):
            config = tf.compat.v1.ConfigProto(allow_soft_placement=True)
            self.sess = tf.compat.v1.Session(config=config)

            # Input variables
            self.node_X = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._nodes_vocab_size), name='node_X')
            self.types = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._types_size), name='types')
            self.Wt = tf.Variable(tf.random.uniform([self._types_size,
                                                     self._types_proj_size], -_rw, _rw))
            self.bt = tf.Variable(tf.random.uniform([self._types_proj_size], -_rw, _rw))
            #problem tf.nn
            
            self.types_projection = lambda x: tf.nn.relu(tf.matmul(x, self.Wt) + self.bt)
            self.types_internal = tf.map_fn(self.types_projection, self.types)
            self.question_vectors_fw = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._question_vocab_size),
                                                      name='question_vectors_inp_fw')
            self.question_vectors_bw = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._question_vocab_size),
                                                      name='question_vectors_inp_nw')
            self.question_mask = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._mask_size),
                                                name='question_mask')

            # The question is pre-processed by a bi-GRU
            self.Wq = tf.Variable(tf.random.uniform([self._question_vocab_size,
                                                     self._word_proj_size_for_rnn], -_rw, _rw))
            self.bq = tf.Variable(tf.random.uniform([self._word_proj_size_for_rnn], -_rw, _rw))
            self.internal_projection = lambda x: tf.nn.relu(tf.matmul(x, self.Wq) + self.bq)
            self.question_int_fw = tf.map_fn(self.internal_projection, self.question_vectors_fw)
            self.question_int_bw = tf.map_fn(self.internal_projection, self.question_vectors_bw)
            
            #problem rnn
            self.rnn_cell_fw = tf.compat.v1.nn.rnn_cell.MultiRNNCell([tf.compat.v1.nn.rnn_cell.GRUCell(self._memory_dim) for _ in range(self._stack_dimension)],
                                                state_is_tuple=True)
            self.rnn_cell_bw = tf.compat.v1.nn.rnn_cell.MultiRNNCell([tf.compat.v1.nn.rnn_cell.GRUCell(self._memory_dim) for _ in range(self._stack_dimension)],
                                                state_is_tuple=True)
            with tf.compat.v1.variable_scope('fw'):
                #problem dynamic rnn
                output_fw, state_fw = tf.compat.v1.nn.dynamic_rnn(self.rnn_cell_fw, self.question_int_fw, time_major=True,
                                                        dtype=tf.float32)
            with tf.compat.v1.variable_scope('bw'):
                #problem dynamen rnn
                output_bw, state_bw = tf.compat.v1.nn.dynamic_rnn(self.rnn_cell_bw, self.question_int_bw, time_major=True,
                                                        dtype=tf.float32)

            self.states = tf.concat(values=[output_fw, tf.reverse(output_bw, [0])], axis=2)
            self.question_vector_pre = tf.reduce_mean(tf.multiply(self.question_mask, self.states), axis=0)
            self.Wqa = tf.Variable(
                tf.random.uniform([2 * self._memory_dim, self._question_vector_size], -_rw, _rw),
                name='Wqa')
            self.bqa = tf.Variable(tf.random.uniform([self._question_vector_size], -_rw, _rw), name='bqa')
            #problem tf.nn
            self.question_vector = tf.nn.relu(tf.matmul(self.question_vector_pre, self.Wqa) + self.bqa)

            # Dense layer before gcn
            self.Wi = tf.Variable(tf.random.uniform([self._nodes_vocab_size,
                                                     self._word_proj_size], -_rw, _rw))
            self.bi = tf.Variable(tf.random.uniform([self._word_proj_size], -_rw, _rw))
            self.internal_projection2 = lambda x: tf.nn.relu(tf.matmul(x, self.Wi) + self.bi)
            self.word_embeddings = tf.map_fn(self.internal_projection2, self.node_X)

            self.inputs = tf.concat(values=[self.word_embeddings, self.types_internal], axis=2)
            self.Wp = tf.Variable(tf.random.uniform([self._word_proj_size + self._types_proj_size,
                                                     self._internal_proj_size], -_rw, _rw))
            self.bp = tf.Variable(tf.random.uniform([self._internal_proj_size], -_rw, _rw))
            self.enc_int_projection = lambda x: tf.nn.relu(tf.matmul(x, self.Wp) + self.bp)
            self.enc_int = tf.map_fn(self.enc_int_projection, self.inputs)

            # GCN part
            self.Atilde_fw = tf.nn.dropout(tf.compat.v1.placeholder(tf.float32, shape=(None, None, None), name="Atilde_fw"), 0.25)

            self.X1_fw = GCN_layer_fw(self._internal_proj_size,
                                      self._hidden_layer1_size,
                                      self._question_vector_size,
                                      self.enc_int,
                                      self.Atilde_fw,
                                      self.question_vector,
                                      '_1')
            #problem tf.nn
            self.X1_fw_dropout = tf.nn.dropout(self.X1_fw, dropout)

            self.X2_fw = GCN_layer_fw(self._hidden_layer1_size,
                                      self._hidden_layer1_size,
                                      self._question_vector_size,
                                      self.X1_fw_dropout,
                                      self.Atilde_fw,
                                      self.question_vector,
                                      '_2')
            self.X2_fw_dropout = tf.nn.dropout(self.X2_fw, dropout)

            self.X3_fw = GCN_layer_fw(self._hidden_layer1_size,
                                      self._hidden_layer1_size,
                                      self._question_vector_size,
                                      self.X2_fw_dropout,
                                      self.Atilde_fw,
                                      self.question_vector,
                                      '_3')
            self.X3_fw_dropout = tf.nn.dropout(self.X3_fw, dropout)

            self.X4_fw = GCN_layer_fw(self._hidden_layer1_size,
                                      self._hidden_layer1_size,
                                      self._question_vector_size,
                                      self.X3_fw_dropout,
                                      self.Atilde_fw,
                                      self.question_vector,
                                      '_4')
            #tf.nn
            self.X4_fw_dropout = tf.nn.dropout(self.X4_fw, dropout)
            self.first_node = self.X4_fw_dropout[0]
            self.concatenated = tf.concat(values=[self.question_vector, self.first_node], axis=1)

            # Final feedforward layers
            self.Ws1 = tf.Variable(
                tf.random.uniform([self._question_vector_size
                                   + self._hidden_layer1_size,
                                   self._hidden_layer2_size], -_rw, _rw),
                name='Ws1')
            self.bs1 = tf.Variable(tf.random.uniform([self._hidden_layer2_size], -_rw, _rw), name='bs1')
            #problem tf.nn
            self.first_hidden = tf.nn.relu(tf.matmul(self.concatenated, self.Ws1) + self.bs1)
            self.first_hidden_dropout = tf.nn.dropout(self.first_hidden, dropout)

            self.Wf = tf.Variable(
                tf.random.uniform([self._hidden_layer2_size, self._output_size], -_rw,
                                  _rw),
                name='Wf')
            self.bf = tf.Variable(tf.random.uniform([self._output_size], -_rw, _rw), name='bf')
            #problem tf.nn
            self.outputs = tf.nn.softmax(tf.matmul(self.first_hidden_dropout, self.Wf) + self.bf)

            # Loss function and training
            self.y_ = tf.compat.v1.placeholder(tf.float32, shape=(None, self._output_size), name='y_')
            self.outputs2 = tf.squeeze(self.outputs)
            self.y2_ = tf.squeeze(self.y_)
            self.one = tf.ones_like(self.outputs)
            self.tiny = self.one * TINY
            self.cross_entropy = (tf.reduce_mean(
                -tf.reduce_sum(self.y_ * tf.compat.v1.log(self.outputs + self.tiny) * _weight_for_positive_matches
                               + (self.one - self.y_) * tf.compat.v1.log(
                    self.one - self.outputs + self.tiny))
            ))

        # Clipping the gradient
        optimizer = tf.compat.v1.train.AdamOptimizer(1e-4)
        gvs = optimizer.compute_gradients(self.cross_entropy)
        capped_gvs = [(tf.clip_by_value(grad, -1., 1.), var) for grad, var in gvs if var.name.find(NAMESPACE) != -1]
        self.train_step = optimizer.apply_gradients(capped_gvs)
        self.sess.run(tf.compat.v1.global_variables_initializer())

        # Adding the summaries
        tf.summary.scalar('cross_entropy', self.cross_entropy)
        self.merged = tf.compat.v1.summary.merge_all(key=tf.compat.v1.GraphKeys.SUMMARIES)
        self.train_writer = tf.compat.v1.summary.FileWriter('./train', self.sess.graph)

    def _add_identity(self, A):
        num_nodes = A.shape[0]
        identity = np.identity(num_nodes)
        return identity + A

    def __train(self, A_fw, node_X, types, item_vector, question_vectors, question_mask, y):
        item_vector = np.array(item_vector)
        Atilde_fw = np.array([self._add_identity(item) for item in A_fw])
        print(node_X.shape)
        node_X = np.array(node_X)
        
        node_X = np.transpose(node_X, (1, 0, 2))

        types = np.array(types)
        types = np.transpose(types, (1, 0, 2))

        question_vectors = np.array(question_vectors)
        question_vectors_fw = np.transpose(question_vectors, (1, 0, 2))
        question_vectors_bw = question_vectors_fw[::-1, :, :]

        question_mask = np.array(question_mask)
        question_mask = np.transpose(question_mask, (1, 0, 2))

        y = np.array(y)

        feed_dict = {}
        feed_dict.update({self.node_X: node_X})
        feed_dict.update({self.types: types})
        feed_dict.update({self.question_vectors_fw: question_vectors_fw})
        feed_dict.update({self.question_vectors_bw: question_vectors_bw})
        feed_dict.update({self.question_mask: question_mask})
        feed_dict.update({self.Atilde_fw: Atilde_fw})
        feed_dict.update({self.y_: y})
        loss, _,outputs2, y2 = self.sess.run(
            [self.cross_entropy, self.train_step,  self.outputs2, self.y2_], feed_dict)
        return loss

    def train(self, data, epochs=20):
        losses = []
        
#         print(type(data[0][6]))
        for epoch in range(epochs):
        
            loss = self.__train([data[i][0] for i in range(len(data))],
                                   [data[i][1] for i in range(len(data))],
                                   [data[i][2] for i in range(len(data))],
                                   [data[i][3] for i in range(len(data))],
                                   [data[i][4] for i in range(len(data))],
                                   [data[i][5] for i in range(len(data))],
                                   [data[i][6] for i in range(len(data))])

#             print(loss)
            losses.append(loss)
            
            sys.stdout.flush()
        return losses

    def __predict(self, A_fw, node_X, types, item_vector, question_vectors, question_mask):
        item_vector = np.array(item_vector)
        Atilde_fw = np.array([self._add_identity(item) for item in A_fw])

        node_X = np.array(node_X)
        node_X = np.transpose(node_X, (1, 0, 2))

        types = np.array(types)
        types = np.transpose(types, (1, 0, 2))

        question_vectors = np.array(question_vectors)
        question_vectors_fw = np.transpose(question_vectors, (1, 0, 2))
        question_vectors_bw = question_vectors_fw[::-1, :, :]

        question_mask = np.array(question_mask)
        question_mask = np.transpose(question_mask, (1, 0, 2))

        feed_dict = {}
        feed_dict.update({self.node_X: node_X})
        feed_dict.update({self.types: types})
        feed_dict.update({self.question_vectors_fw: question_vectors_fw})
        feed_dict.update({self.question_vectors_bw: question_vectors_bw})
        feed_dict.update({self.question_mask: question_mask})
        feed_dict.update({self.Atilde_fw: Atilde_fw})

        y_batch = self.sess.run([self.outputs2], feed_dict)
        return y_batch

    def __standardize_item(self, item):
        if item[0] < item[1]:
            return [0., 1.]
        return [1., 0.]

    def predict(self, A_fw, node_X, types, item_vector, question_vectors, question_mask):
        output = self.__predict([A_fw], [node_X], [types], [item_vector], [question_vectors], [question_mask])
        return self.__standardize_item(output[0])

    # Loading and saving functions

    def save(self, filename):
        saver = tf.compat.v1.train.Saver()
        saver.save(self.sess, filename)

    def load_tensorflow(self, filename):
        saver =tf.compat.v1.train.Saver([v for v in tf.compat.v1.global_variables() if NAMESPACE in v.name])
        saver.restore(self.sess, filename)

    @classmethod
    def load(self, filename, dropout=0.25):
        model = GCN_QA(dropout)
        model.load_tensorflow(filename)
        return model

In [30]:
def train(data, model, saving_dir, name_prefix, epochs=20, bucket_size=10, trace_every=1):
    

    buckets = bin_data_into_buckets(data, bucket_size)

    losses = []
    for i in range(epochs):
        random_buckets = sorted(buckets, key=lambda x: random.random())
        sys.stderr.write('--------- Epoch ' + str(i) + ' ---------\n')
        for bucket in random_buckets:
            graph_bucket = []
            
#             try:
            for item in bucket:
                node_vectors = item['graph']['vectors']
                types = item['graph']['types']
                A_bw = item['graph']['A_bw']
                y = item['answer']
                item_vector = item['item_vector']
                question_vectors = item['question_vectors']
                question_mask = item['question_mask']
                graph_bucket.append((A_bw, node_vectors, types, item_vector, question_vectors, question_mask, y))
            if len(graph_bucket) > 0:
                loss = model.train(graph_bucket, 1)
                losses.append(loss)
#             except Exception as e:
#                 print('Exception caught during training: ' + str(e))
        if i % trace_every == 0:
            save_filename = saving_dir + name_prefix + '-' + str(i) + '.tf'
            sys.stderr.write('Saving into ' + save_filename + '\n')
            model.save(save_filename)
    return losses
    

AttributeError: module 'os' has no attribute 'get_cwd'

In [21]:
_bucket_size = 10
_minimum_trace = 10
with open(os.path.join('Compute metrics/dataset/wikidata-disambig-train.json')) as f:
    json_data = json.load(f)
training_data, lost = get_json_data(json_data,10000)

print(len(training_data))
print(len(lost))

lost[0]

nodelist: 'gnaeus pompeius|NODE' is not in list
nodelist: 'lee jong-wook|NODE' is not in list
nodelist: 'right angle|NODE' is not in list
nodelist: 'vitamin c|NODE' is not in list
nodelist: "people's party|NODE" is not in list
nodelist: 'programming language|NODE' is not in list
nodelist: 'south asia|NODE' is not in list
nodelist: 'programmer|NODE' is not in list
nodelist: 'wiki|NODE' is not in list
nodelist: 'richmond park|NODE' is not in list
nodelist: 'tracy reed|NODE' is not in list
nodelist: 'mathematics|NODE' is not in list
nodelist: 'reason|NODE' is not in list
nodelist: 'augustus|NODE' is not in list
nodelist: 'new democracy|NODE' is not in list
nodelist: 'old turkic|NODE' is not in list
nodelist: 'rome|NODE' is not in list
nodelist: 'the silence of the lambs|NODE' is not in list
nodelist: 'culture|NODE' is not in list
nodelist: 'persian gulf|NODE' is not in list
nodelist: 'tom river|NODE' is not in list
nodelist: 'linköping|NODE' is not in list
nodelist: 'brandenburg|NODE' is 

{'correct_id': 'Q102083',
 'string': 'knight',
 'text': " knight rendered in Art Deco style holding a crusader's sword standing on a reel of film with five spokes. The five spokes each represent the original branches of the Academy: Actors, ",
 'wrong_id': 'Q17057554'}

### 

In [23]:
import random
import sys
print('Loading model: ')
_saving_dir = 'data\\'
nn_model_gcn_with_attention = GCN_QA(dropout=0.25)
losses = train(training_data,
      nn_model_gcn_with_attention,
      _saving_dir,
      name_prefix='qa',
      epochs=10,
      bucket_size=10,
      trace_every=1,
      )


Loading model: 


NameError: name 'GCN_QA' is not defined

In [23]:
def test(data, model):
    true_positives = 0
    false_positives = 0
    true_negatives = 0
    false_negatives = 0
    for item in data:
        node_vectors = item['graph']['vectors']
        types = item['graph']['types']
        A_bw = item['graph']['A_bw']
        expected = item['answer']
        item_vector = item['item_vector']
        question_vectors = item['question_vectors']
        question_mask = item['question_mask']
#        try:
        prediction = model.predict(A_bw, node_vectors, types, item_vector, question_vectors, question_mask)
        if prediction == expected and expected == _is_relevant:
            true_positives += 1
        if prediction == expected and expected == _is_not_relevant:
            true_negatives += 1
        if prediction != expected and expected == _is_relevant:
            false_negatives += 1
        if prediction != expected and expected == _is_not_relevant:
            false_positives += 1
#        except Exception as e:
#            print('Exception caught during training: ' + str(e))
    try:
        precision = true_positives / (true_positives + false_positives)
        recall = true_positives / (true_positives + false_negatives)
        f1 = 2 * 1 / (1 / precision + 1 / recall)
        print('precision', precision)
        print('recall', recall)
        print('f1', f1)
    except:
        print('Cannot compute precision and recall.')





In [24]:
with open(os.path.join('Compute metrics/dataset/wikidata-disambig-test.json')) as f:
    json_data = json.load(f)
test_data,test_lost = get_json_data(json_data,2000)
test(test_data, nn_model_gcn_with_attention)

KeyboardInterrupt: 

In [70]:
test(test_data, nn_model_gcn_with_attention)

precision 0.9477351916376306
recall 0.8690095846645367
f1 0.9066666666666666


In [71]:
print(len(test_data))
print(len(test_lost))

328
1985


### Save training and test data

In [73]:
import pickle 

# Store data (serialize)
with open('training_data_{}.pickle'.format(str(len(training_data))), 'wb') as handle:
    pickle.dump(training_data, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('test_data_{}.pickle'.format(str(len(test_data))), 'wb') as handle:
    pickle.dump(test_data, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [85]:
not 100 % 100 

True

In [106]:
from time import sleep, time
from SPARQLWrapper import SPARQLWrapper, JSON


def infer_vector_from_vector_nodes_rnn(vector_list):
    vector = np.zeros(300)
    return vector

def create_vectors_from_triplets_rnn(triplets, model):
    return [np.concatenate([
        infer_vector_from_doc(model, item[0]),
        infer_vector_from_doc(model, item[1]),
        infer_vector_from_doc(model, item[2])])
        for item in triplets]


def get_adjacency_matrices_and_vectors_given_triplets_rnn(triplets, central_item, model):
    vectors = create_vectors_from_triplets_rnn(triplets, model)
    return {'vectors': vectors}

def get_graph_from_wikidata_id_rnn(wikidata_id, central_item):
 #   url = 'https://query.wikidata.org/bigdata/namespace/wdq/sparql'
#    data = requests.get(url, params={'query': _query % wikidata_id, 'format': 'json'}).json()

    url = 'https://query.wikidata.org/bigdata/namespace/wdq/sparql?query=' + _query % wikidata_id
    

    sparql = SPARQLWrapper("https://query.wikidata.org/sparql")
    # From https://www.wikidata.org/wiki/Wikidata:SPARQL_query_service/queries/examples#Cats
    sparql.setQuery(_query % wikidata_id)
    sparql.setReturnFormat(JSON)
    data = sparql.query().convert()
    triplets = []
    for item in data['results']['bindings']:
        try:
            from_item =translate_from_url(wikidata_id)
            relation = translate_from_url(item['rel']['value'])
            to_item = translate_from_url(item['item']['value'])
            triplets.append((from_item, relation, to_item))
        except:
            pass
        try:
            from_item = translate_from_url(item['item']['value'])
            relation =translate_from_url(item['rel2']['value'])
            to_item = translate_from_url(item['to_item']['value'])
            triplets.append((from_item, relation, to_item))
        except:
            pass
    triplets = sorted(list(set(triplets)))
    if not triplets:
        raise RuntimeError("This graph contains no suitable triplets.")
    return get_adjacency_matrices_and_vectors_given_triplets_rnn(triplets, central_item, model)



def create_text_item_graph_dict_rnn(text, item, wikidata_id):
    text_item_graph_dict = {}
    text_item_graph_dict['text'] = text
    text_item_graph_dict['item'] = item
    text_item_graph_dict['wikidata_id'] = wikidata_id
    text_item_graph_dict['graph'] = get_graph_from_wikidata_id_rnn(wikidata_id, item)
    # text_item_graph_dict['item_vector'] = infer_vector_from_doc(_model, item)
    text_item_graph_dict['item_vector'] = infer_vector_from_vector_nodes_rnn(text_item_graph_dict['graph']['vectors'])
    text_item_graph_dict['question_vectors'] = convert_text_into_vector_sequence(model, text)
    text_item_graph_dict['question_mask'] = get_item_mask_for_words(text, item)
    return text_item_graph_dict

def get_json_data_rnn(json_data, count):
    data = []
    lost=[]
    i = 0 
    
    start_time = time()

    for  json_item in json_data[:count]:
        
        sleep(2.5)
        print(json_item['string'],'          ', i/count)

        if not i % 100:
            print('\n')
            print('time_elapsed (s): ' + str(time() - start_time) + '\n')
            print('\n')
        i+=1
        try:
       

            text = json_item['text']
            item = json_item['string']

            wikidata_id = json_item['correct_id']
    #             print('before problem {}'.format(i))
            text_item_graph_dict = create_text_item_graph_dict_rnn(text, item, wikidata_id)
    #             print('before problem if not with graph {}'.format(i))
            text_item_graph_dict['answer'] = _is_relevant
    #             print('before problem if not with answer {}'.format(i))
            data.append(text_item_graph_dict)

            wikidata_id = json_item['wrong_id']
            text_item_graph_dict = create_text_item_graph_dict_rnn(text, item, wikidata_id)
            text_item_graph_dict['answer'] = _is_not_relevant

            if i < 1:
                print(text_item_graph_dict)
            data.append(text_item_graph_dict)
        except Exception as e:
            print(str(e))
#             break
            lost.append(json_item)
    return data, lost

In [95]:
TINY = 1e-6
ONE = tf.constant(1.)
NAMESPACE = 'rnn'
forbidden_weight = 1.
_weight_for_positive_matches = 1.
_rw = 1e-1


class RNN(object):
    _nodes_vocab_size = 300 * 3
    _question_vocab_size = 300
    _question_vector_size = 150
    _types_size = 3
    _mask_size = 200
    _types_proj_size = 5
    _word_proj_size = 50
    _word_proj_size_for_rnn = 50
    _word_proj_size_for_item = 50
    _internal_proj_size = 250
    _hidden_layer1_size = 250
    _hidden_layer2_size = 250
    _output_size = 2

    _memory_dim = 100
    _stack_dimension = 2

    def __init__(self, dropout=1.0):
        tf.compat.v1.reset_default_graph()
        with tf.compat.v1.variable_scope(NAMESPACE):
            config = tf.compat.v1.ConfigProto(allow_soft_placement=True)
            self.sess = tf.compat.v1.Session(config=config)

            # Input variables
            self.node_X_fw = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._nodes_vocab_size), name='node_X_fw')
            self.node_X_bw = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._nodes_vocab_size), name='node_X_bw')
            self.question_vectors_fw = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._question_vocab_size),
                                                      name='question_vectors_inp_fw')
            self.question_vectors_bw = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._question_vocab_size),
                                                      name='question_vectors_inp_nw')
            self.question_mask = tf.compat.v1.placeholder(tf.float32, shape=(None, None, self._mask_size),
                                                name='question_mask')

            # The question is pre-processed by a bi-GRU
            self.Wq = tf.Variable(tf.compat.v1.random_uniform([self._question_vocab_size,
                                                     self._word_proj_size_for_rnn], -_rw, _rw))
            self.bq = tf.Variable(tf.compat.v1.random_uniform([self._word_proj_size_for_rnn], -_rw, _rw))
            self.internal_projection = lambda x: tf.nn.relu(tf.matmul(x, self.Wq) + self.bq)
            self.question_int_fw = tf.map_fn(self.internal_projection, self.question_vectors_fw)
            self.question_int_bw = tf.map_fn(self.internal_projection, self.question_vectors_bw)

            self.rnn_cell_fw = tf.compat.v1.nn.rnn_cell.MultiRNNCell([tf.compat.v1.nn.rnn_cell.GRUCell(self._memory_dim) for _ in range(self._stack_dimension)],
                                                state_is_tuple=True)
            self.rnn_cell_bw = tf.compat.v1.nn.rnn_cell.MultiRNNCell([tf.compat.v1.nn.rnn_cell.GRUCell(self._memory_dim) for _ in range(self._stack_dimension)],
                                                state_is_tuple=True)
            with tf.compat.v1.variable_scope('fw'):
                output_fw, state_fw = tf.compat.v1.nn.dynamic_rnn(self.rnn_cell_fw, self.question_int_fw, time_major=True,
                                                        dtype=tf.float32)
            with tf.compat.v1.variable_scope('bw'):
                output_bw, state_bw = tf.compat.v1.nn.dynamic_rnn(self.rnn_cell_bw, self.question_int_bw, time_major=True,
                                                        dtype=tf.float32)

            self.states = tf.concat(values=[output_fw, tf.reverse(output_bw, [0])], axis=2)
            self.question_vector_pre = tf.reduce_mean(tf.multiply(self.question_mask, self.states), axis=0)
            self.Wqa = tf.Variable(
                tf.compat.v1.random_uniform([2 * self._memory_dim, self._question_vector_size], -_rw, _rw),
                name='Wqa')
            self.bqa = tf.Variable(tf.compat.v1.random_uniform([self._question_vector_size], -_rw, _rw), name='bqa')
            self.question_vector = tf.nn.relu(tf.matmul(self.question_vector_pre, self.Wqa) + self.bqa)

            # bi-LSTM of triplets part
            self.Wtri = tf.Variable(tf.compat.v1.random_uniform([self._nodes_vocab_size,
                                                       self._word_proj_size_for_rnn], -_rw, _rw))
            self.btri = tf.Variable(tf.compat.v1.random_uniform([self._word_proj_size_for_rnn], -_rw, _rw))
            self.internal_projection = lambda x: tf.nn.relu(tf.matmul(x, self.Wtri) + self.btri)
            self.node_int_fw = tf.map_fn(self.internal_projection, self.node_X_fw)
            self.node_int_bw = tf.map_fn(self.internal_projection, self.node_X_bw)

            self.rnn_cell_fw_tri = tf.compat.v1.nn.rnn_cell.MultiRNNCell(
                [tf.compat.v1.nn.rnn_cell.GRUCell(self._memory_dim) for _ in range(self._stack_dimension)],
                state_is_tuple=True)
            self.rnn_cell_bw_tri = tf.compat.v1.nn.rnn_cell.MultiRNNCell(
                [tf.compat.v1.nn.rnn_cell.GRUCell(self._memory_dim) for _ in range(self._stack_dimension)],
                state_is_tuple=True)
            with tf.compat.v1.variable_scope('fw_tri'):
                output_fw_tri, _ = tf.compat.v1.nn.dynamic_rnn(self.rnn_cell_fw_tri, self.node_int_fw, time_major=True,
                                                     dtype=tf.float32)
            with tf.compat.v1.variable_scope('bw_tri'):
                output_bw_tri, _ = tf.compat.v1.nn.dynamic_rnn(self.rnn_cell_bw_tri, self.node_int_bw, time_major=True,
                                                     dtype=tf.float32)

            self.states_tri = tf.concat(values=[output_fw_tri, output_bw_tri], axis=2)

            self.Walpha = tf.Variable(tf.compat.v1.random_uniform([2 * self._memory_dim + self._question_vector_size,
                                                         1], -_rw, _rw))
            self.balpha = tf.Variable(tf.compat.v1.random_uniform([1], -_rw, _rw))
            self.alpha_projection = lambda x: tf.nn.relu(tf.matmul(tf.concat(values=[x, self.question_vector], axis=1),
                                                                   self.Walpha) + self.balpha)
            self.alphas = tf.map_fn(self.alpha_projection, self.states_tri)
            self.alphas = tf.compat.v1.nn.softmax(self.alphas, dim =0)
            self.centroid = tf.reduce_mean(tf.multiply(self.states_tri, self.alphas), axis=0)

            self.concatenated = tf.concat(values=[self.question_vector, self.centroid], axis=1)

            # Final feedforward layers
            self.Ws1 = tf.Variable(
                tf.compat.v1.random_uniform([self._question_vector_size
                                   + 2 * self._memory_dim,
                                   self._hidden_layer2_size], -_rw, _rw),
                name='Ws1')
            self.bs1 = tf.Variable(tf.compat.v1.random_uniform([self._hidden_layer2_size], -_rw, _rw), name='bs1')
            self.first_hidden = tf.nn.relu(tf.matmul(self.concatenated, self.Ws1) + self.bs1)
            self.first_hidden_dropout = tf.nn.dropout(self.first_hidden, dropout)

            self.Wf = tf.Variable(
                tf.compat.v1.random_uniform([self._hidden_layer2_size, self._output_size], -_rw,
                                  _rw),
                name='Wf')
            self.bf = tf.Variable(tf.compat.v1.random_uniform([self._output_size], -_rw, _rw), name='bf')
            self.outputs = tf.nn.softmax(tf.matmul(self.first_hidden_dropout, self.Wf) + self.bf)

            # Loss function and training
            self.y_ = tf.compat.v1.placeholder(tf.float32, shape=(None, self._output_size), name='y_')
            self.outputs2 = tf.squeeze(self.outputs)
            self.y2_ = tf.squeeze(self.y_)
            self.one = tf.ones_like(self.outputs)
            self.tiny = self.one * TINY
            self.cross_entropy = (tf.reduce_mean(
                -tf.reduce_sum(self.y_ * tf.compat.v1.log(self.outputs + self.tiny) * _weight_for_positive_matches
                               + (self.one - self.y_) * tf.compat.v1.log(
                    self.one - self.outputs + self.tiny))
            ))

        # Clipping the gradient
        optimizer = tf.compat.v1.train.AdamOptimizer(1e-4)
        gvs = optimizer.compute_gradients(self.cross_entropy)
        capped_gvs = [(tf.clip_by_value(grad, -1., 1.), var) for grad, var in gvs if var.name.find(NAMESPACE) != -1]
        self.train_step = optimizer.apply_gradients(capped_gvs)
        self.sess.run(tf.compat.v1.global_variables_initializer())

        # Adding the summaries
        tf.compat.v1.summary.scalar('cross_entropy', self.cross_entropy)
        self.merged = tf.compat.v1.summary.merge_all(key=tf.compat.v1.GraphKeys.SUMMARIES)
        self.train_writer = tf.compat.v1.summary.FileWriter('./train', self.sess.graph)

    def __train(self, node_X, item_vector, question_vectors, question_mask, y):
        node_X_fw = np.array(node_X)
        node_X_fw = np.transpose(node_X_fw, (1, 0, 2))
        node_X_bw = node_X_fw[::-1, :, :]

        question_vectors = np.array(question_vectors)
        question_vectors_fw = np.transpose(question_vectors, (1, 0, 2))
        question_vectors_bw = question_vectors_fw[::-1, :, :]

        question_mask = np.array(question_mask)
        question_mask = np.transpose(question_mask, (1, 0, 2))

        y = np.array(y)

        feed_dict = {}
        feed_dict.update({self.node_X_fw: node_X_fw})
        feed_dict.update({self.node_X_bw: node_X_bw})
        feed_dict.update({self.question_vectors_fw: question_vectors_fw})
        feed_dict.update({self.question_vectors_bw: question_vectors_bw})
        feed_dict.update({self.question_mask: question_mask})
        feed_dict.update({self.y_: y})

        loss, _,  outputs2, y2 = self.sess.run(
            [self.cross_entropy, self.train_step, self.outputs2, self.y2_], feed_dict)
        return loss

    def train(self, data, epochs=20):
        
        for epoch in range(epochs):
            loss = self.__train([data[i][0] for i in range(len(data))],
                                   [data[i][1] for i in range(len(data))],
                                   [data[i][2] for i in range(len(data))],
                                   [data[i][3] for i in range(len(data))],
                                   [data[i][4] for i in range(len(data))])

            sys.stdout.flush()
        return loss
    def __predict(self, node_X, item_vector, question_vectors, question_mask):
        
        node_X_fw = np.array(node_X)
        node_X_fw = np.transpose(node_X_fw, (1, 0, 2))
        node_X_bw = node_X_fw[::-1, :, :]

        question_vectors = np.array(question_vectors)
        question_vectors_fw = np.transpose(question_vectors, (1, 0, 2))
        question_vectors_bw = question_vectors_fw[::-1, :, :]

        question_mask = np.array(question_mask)
        question_mask = np.transpose(question_mask, (1, 0, 2))

        feed_dict = {}
        feed_dict.update({self.node_X_fw: node_X_fw})
        feed_dict.update({self.node_X_bw: node_X_bw})

        feed_dict.update({self.question_vectors_fw: question_vectors_fw})
        feed_dict.update({self.question_vectors_bw: question_vectors_bw})
        feed_dict.update({self.question_mask: question_mask})

        y_batch = self.sess.run([self.outputs2], feed_dict)
        return y_batch

    def __standardize_item(self, item):
        if item[0] < item[1]:
            return [0., 1.]
        return [1., 0.]

    def predict(self, node_X, item_vector, question_vectors, question_mask):
        output = self.__predict([node_X], [item_vector], [question_vectors], [question_mask])
        return self.__standardize_item(output[0])

    # Loading and saving functions

    def save(self, filename):
        saver =  tf.compat.v1.train.Saver()
        saver.save(self.sess, filename)

    def load_tensorflow(self, filename):
        saver =  tf.compat.v1.train.Saver([v for v in tf.compat.v1.global_variables() if NAMESPACE in v.name])
        saver.restore(self.sess, filename)

    @classmethod
    def load(self, filename, dropout=1.0):
        model = GCN_QA(dropout)
        model.load_tensorflow(filename)
        return model


In [96]:
def train_rnn(data, model, saving_dir, name_prefix, epochs=20, bucket_size=10, trace_every=1):
    buckets = bin_data_into_buckets(data, bucket_size)
    losses = []
    for i in range(epochs):
        random_buckets = sorted(buckets, key=lambda x: random.random())
        sys.stderr.write('--------- Epoch ' + str(i) + ' ---------\n')
       
        for bucket in random_buckets:
            graph_bucket = []
#             try:
            for item in bucket:
                node_vectors = item['graph']['vectors']
                y = item['answer']
                item_vector = item['item_vector']
                question_vectors = item['question_vectors']
                question_mask = item['question_mask']
#                 print('node_vector: {}'.format(type(node_vectors)))
#                 print('y: {}'.format(y))
#                 print('item_vector: {}'.format(type(item_vector)))
#                 print('question_vectors: {}'.format(type(question_vectors)))
#                 print('question_mask: {}'.format(type(question_mask)))
#                 break
                graph_bucket.append((node_vectors, item_vector, question_vectors, question_mask, y))
                
                
            if len(graph_bucket) > 0:
                loss = model.train(graph_bucket, 1)
                losses.append(loss)
#             except Exception as e:
#                 print('Exception caught during training: ' + str(e))
        if i % trace_every == 0:
            save_filename = saving_dir + name_prefix + '-' + str(i) + '.tf'
            sys.stderr.write('Saving into ' + save_filename + '\n')
            model.save(save_filename)
    return losses, buckets

In [97]:
print(3)

3


In [25]:
tf.compat.v1.disable_eager_execution()

print('Loading model: ')
RNN_with_attention = RNN(dropout=0.25)
_saving_dir = 'data/'
losses_ru, bucket = train_rnn(training_data_rnn,
      RNN_with_attention,
      _saving_dir,
      name_prefix='rnn',
      epochs=1,
      bucket_size=10,
      trace_every=1,
      )


Loading model: 


--------- Epoch 0 ---------
Saving into data/rnn-0.tf


In [31]:
saver = tf.compat.v1.train.Saver()

In [36]:
sess = tf.compat.v1.Session()

### Load the data set for RNN. 

It's 20,000 sets with 10 nodes per subgraph.

baseline.


In [15]:
import pickle
# Store data (serialize)
with open('training_data_rnn_3630.pickle', 'rb') as handle:
    training_data_rnn = pickle.load(handle)


Select 5000 of the entities already in the baseline, to 

#### Generate different data sets, for different number of nodes.

- max nodes is easy to tune 

In [100]:
n_entities = 5000

for max_nodes in [400]:
    
    _query = '''
    SELECT ?rel ?item ?rel2 ?to_item {
      wd:%s ?rel ?item
      OPTIONAL { ?item ?rel2 ?to_item }
      FILTER regex (str(?item), '^((?!statement).)*$') .
      FILTER regex (str(?item), '^((?!https).)*$') .
    } LIMIT 
    ''' + str(max_nodes)
    
    
    _bucket_size = 10
    _minimum_trace = 10
  #  with open(os.path.join('Compute metrics/dataset/wikidata-disambig-train.json')) as f:
   #     json_data = json.load(f)
    training_data_rnn, training_data_rnn_lost = get_json_data_rnn(json_data,n_entities)
     

    # Store data (serialize)
    with open('training_data_rnn_{}.pickle'.format(str(len(training_data_rnn)) + '_' + str(max_nodes)), 'wb') as handle:
        pickle.dump(training_data_rnn, handle, protocol=pickle.HIGHEST_PROTOCOL)
    

captain marvel            0.0


time_elapsed (s): 2.5023701190948486





IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



corfu            0.0002


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



hera            0.0004
{'text': " a tale which offers an alternative version of these events: in Argonautica (iv.760) Hera alludes to Thetis's chaste resistance to the advances of Zeus, that Thetis was so loyal ", 'item': 'hera', 'wikidata_id': 'Q37162645', 'graph': {'vectors': [array([ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.0

...

liverpool            0.7288
mitch mitchell            0.729
monty python's flying circus            0.7292
doctor at large            0.7294
barbara            0.7296
emperor            0.7298
carl nielsen            0.73
oxford            0.7302
hera            0.7304
virgil            0.7306
discovery            0.7308
liberia            0.731
violin concerto            0.7312
oratorio            0.7314
manhattan            0.7316
soho            0.7318
madonna            0.732
new york city            0.7322
political science            0.7324
corporation            0.7326
society            0.7328
lessing            0.733
pride            0.7332
separation of powers            0.7334
geneva            0.7336
the phantom of the opera            0.7338
chris penn            0.734
maurice couve de murville            0.7342
roman empire            0.7344
mississippi            0.7346
saint petersburg            0.7348
paris            0.735
HTTP Error 429: Too Many Requests
amsterdam 

civil war            0.7826
swedish            0.7828
modern english            0.783
denmark            0.7832
stockholm            0.7834
iceland            0.7836
sovereignty            0.7838
pomerania            0.784
denmark            0.7842
finland            0.7844
enol            0.7846
alcohol            0.7848
ammonia            0.785
hypoglycemia            0.7852
pentagram            0.7854
pentagon            0.7856
pentagram            0.7858
pentagram            0.786
libya            0.7862
bible            0.7864
jericho            0.7866
samaria            0.7868
yoshiwara            0.787
kyoto            0.7872
breast cancer            0.7874
the burmese harp            0.7876
fires on the plain            0.7878
tokyo            0.788
pneumonia            0.7882
ankara            0.7884
pakistan            0.7886
purple heart            0.7888
napster            0.789
australia            0.7892
copyright            0.7894
deposition            0.7896
manchester 

thuringia            0.8396
botanical garden            0.8398
ware            0.84


time_elapsed (s): 16473.227669000626



kikuyu            0.8402
temperature            0.8404
liquid            0.8406
yorkshire            0.8408
brazil            0.841
ireland            0.8412
barbizon            0.8414
japan            0.8416
computer science            0.8418
caliph            0.842
venus            0.8422
venice            0.8424
latin            0.8426
comedy            0.8428
mythology            0.843
berlin            0.8432
geography            0.8434
pakistan            0.8436
honduras            0.8438
bangladesh            0.844
university of chicago            0.8442
alpaca            0.8444
alpaca            0.8446
alpaca            0.8448
new york            0.845
english            0.8452
stranger in a strange land            0.8454
kazakhstan            0.8456
august 18            0.8458
kuban            0.846
tokyopop            0.8462
constellation            0.

plato            0.896
monty python's flying circus            0.8962
david hume            0.8964
monty python's flying circus            0.8966
codex            0.8968
movable type            0.897
archive            0.8972
performance            0.8974
regional council            0.8976
martinique            0.8978
ballot            0.898
milan            0.8982
mauritania            0.8984
transformer            0.8986
nickel            0.8988
tamil            0.899
gujarati            0.8992
great britain            0.8994
islam            0.8996
russia            0.8998
australia            0.9


time_elapsed (s): 17625.23442697525



indian ocean            0.9002
port louis            0.9004
united kingdom            0.9006
americas            0.9008
álvaro obregón            0.901
oklahoma            0.9012
sinaloa            0.9014
venezuela            0.9016
general motors            0.9018
transnistria            0.902
russia            0.9022
august 27            0.9024
ru

africa            0.954
world war ii            0.9542
madagascar            0.9544
south africa            0.9546
indian ocean            0.9548
perch            0.955
pork            0.9552
nevada            0.9554
nova scotia            0.9556
chile            0.9558
parliament            0.956
ambush            0.9562
colonel            0.9564
spacetime            0.9566
ur            0.9568
institute for advanced study            0.957
graviton            0.9572
hampshire            0.9574
breast cancer            0.9576
machine gun            0.9578
cardiff            0.958
hypoglycemia            0.9582
spin            0.9584
classical mechanics            0.9586
speed            0.9588
force            0.959
pal            0.9592
georgia            0.9594
leros            0.9596
ankara            0.9598
eragon            0.96


time_elapsed (s): 18780.56102991104



20th century fox            0.9602
marketing            0.9604
solar wind            0.9606
australian capital te

In [90]:
len(json_data)

100000

In [57]:
training_data[0].keys()
type(data)

list

In [111]:
max_nodes = 400

_query = '''
    SELECT ?rel ?item ?rel2 ?to_item {
      wd:%s ?rel ?item
      OPTIONAL { ?item ?rel2 ?to_item }
      FILTER regex (str(?item), '^((?!statement).)*$') .
      FILTER regex (str(?item), '^((?!https).)*$') .
    } LIMIT 
    ''' + str(max_nodes)

In [113]:
n_test = 1000

path_to_test_data = 'Compute metrics/dataset/wikidata-disambig-test.json'

with open(os.path.join(path_to_test_data)) as f:
    json_data = json.load(f)
test_data,lost_rnn= get_json_data_rnn(json_data,n_test)


# Store data (serialize)
with open('test_data_{}.pickle'.format(str(model_used) + '_' + str(len(test_data)) + '_' + str(max_nodes)), 'wb') as handle:
    pickle.dump(test_data, handle, protocol=pickle.HIGHEST_PROTOCOL)

# test(data, nn_model_gcn_with_attention)

university            0.0


time_elapsed (s): 2.5089850425720215



nanjing            0.001
english            0.002
harpsichord            0.003
gary cooper            0.004
sustain            0.005
harpsichord            0.006
melbourne            0.007
victoria            0.008
northcote            0.009
victoria            0.01
clifton hill            0.011
australia            0.012
california            0.013
queer            0.014
gender role            0.015
gender role            0.016
egg            0.017
fruit            0.018
india            0.019
california            0.02
san fernando valley            0.021
lead            0.022
victoria            0.023
heidelberg            0.024
australia            0.025
central business district            0.026
HTTP Error 429: Too Many Requests
victoria            0.027
melbourne            0.028
melbourne            0.029
doctor in distress            0.03
no love for johnnie            0.031
colette            0.032
HTTP Error 

renaissance            0.283
taenia            0.284
pediment            0.285
edgbaston            0.286
england            0.287
birmingham            0.288
conservatory            0.289
tenterfield            0.29
australia            0.291
moree            0.292
australia            0.293
amsterdam            0.294
gundagai            0.295
balranald            0.296
mildura            0.297
valencia            0.298
asia            0.299
world war ii            0.3


time_elapsed (s): 1225.32870388031



whale            0.301
june 21            0.302
maitland            0.303
sundial            0.304
franklins            0.305
belford            0.306
melbourne            0.307
victoria            0.308
flemington            0.309
australia            0.31
australia            0.311
echuca            0.312
murray river            0.313
eildon            0.314
communism            0.315
moscow            0.316
kremlin            0.317
soviet union            0.318
HTTP Error 429: 

theft            0.565
english            0.566
finland            0.567
melbourne            0.568
kings park            0.569
refugee            0.57
australia            0.571
quito            0.572
rio de janeiro            0.573
pelé            0.574
são paulo            0.575
pelé            0.576
brazil            0.577
midfielder            0.578
pelé            0.579
pelé            0.58
silver            0.581
distillation            0.582
alchemy            0.583
cancer            0.584
caribbean            0.585
world war ii            0.586
leyte            0.587
london            0.588
yorkshire            0.589
mtv2            0.59
mtv            0.591
120 minutes            0.592
vj            0.593
pernambuco            0.594
january 3            0.595
battle creek            0.596
michigan            0.597
public-key cryptography            0.598
world war ii            0.599
december 8            0.6


time_elapsed (s): 2423.180899143219



jamaica            0.601
g

vhs            0.855
rhythm of love            0.856
better the devil you know            0.857
saturday            0.858
blackburn            0.859
melbourne            0.86
victoria            0.861
mont albert            0.862
australia            0.863
lawyer            0.864
This graph contains no suitable triplets.
blois            0.865
august 11            0.866
may 27            0.867
january 9            0.868
astronomer            0.869
strasbourg            0.87
april 29            0.871
australia            0.872
jurisprudence            0.873
john law            0.874
breathe            0.875
shocked            0.876
australia            0.877
the clash            0.878
set list            0.879
cold war            0.88
election            0.881
canada            0.882
peace            0.883
operating system            0.884
cantata            0.885
conscience            0.886
vilnius            0.887
robert burns            0.888
athenry            0.889
edgbaston       

In [61]:
with open(os.path.join()) as f:
    json_data = json.load(f)
test_data_rnn,lost_rnn= get_json_data_rnn(json_data,5000)
# test(data, nn_model_gcn_with_attention)

The University of Nanking (金陵大学) was a private university in Nanjing, China 
0.0


 private university in Nanjing, China which was founded in 1888 and sponsored by American churches. It's originally named the Nanking University, the first school officially named University (in 
0.0002


 first school officially named University (in English) in China. History. The Nanking University (汇文书院, Huiwen Shuyuan) was founded in 1888 by C.H. Fouler. Initially there were three 
0.0004


 to the German-speaking nations. Silbermann, who worked in Freiberg in Germany, began to make pianos based on Cristofori's design around 1730. (His previous experience had been in building organs, harpsichord
0.0006


 Bart van Oort and Gary Cooper. Opinions. Opinions about fortepiano sound vary widely, both from person to person and from instrument to instrument. Michael Cookson, a reviewer from UK-based MusicWeb-International states 
0.0008


 piano, being softer with less sustain. Sforzando accents tend to stan

Member of Parliament and NHL defenceman who won three Stanley Cups. Jamie McGinn, OHL player of the Ottawa 67's drafted by the San Jose Sharks of the NHL in 2006. Tye McGinn, OHL 
0.0098


string theory, principally extra dimensions, branes and orbifolds. String theory itself is a controversial idea in physics. The Baum–Frampton model. This more recent cyclic model of 2007 makes a different technical assumption 
0.01


 expansion of the universe, is several orders of magnitude smaller than predicted by the standard Big Bang model. A different cyclic model relying on the notion of phantom energy was 
0.0102


 and trees.". Writing. In 1866 he became a fellow of the Linnean Society at the age of 29 under the sponsorship of Charles Darwin, James Veitch, David Moore, and 
0.0104


 in the cleared spaces in the woods, Robinson established plantings of Japanese anemone, lily, acanthus, and Pampas grass, along with shrubs such as fothergilla, stewartia, and nyssa. Closer 
0.0106


 the greenh

 build Beaumaris Castle. It was, literally, established as a 'new borough' and gained its charter in 1303. In the 16th century, Newborough was the county town of Anglesey and 
0.019


 is accepted. A derivative encoding is KOI8-U, which adds Ukrainian characters. The original KOI-8 encoding was designed by Soviet authorities in 1974. KOI8 remains much more commonly used than ISO 
0.0192


 8-bit character encoding, designed to cover Russian, which uses the Cyrillic alphabet. It also happens to cover Bulgarian, but not used since CP1251 is accepted. A derivative encoding is KOI8-U, which 
0.0194


 References. Peter Green, Alexander to Actium (University of California Press, 1990), pp. 553-554 ISBN 0-520-05611-6. External links. entry in historical sourcebook by Mahlon H. Smith.
0.0196


 time. However, Rome's Sulla wanted a pro-Roman ruler on the throne, and sent the young son of Ptolemy X to Egypt, displaying Ptolemy Alexander's will in Rome as justification for 
0.0198


Bradford is 

 of the 20 regions of Finland. Seinäjoki is the regional centre and by far the largest city in the area. Historical provinces. For History, Geography and Culture 
0.028


 of the biggest Rock festivals in Finland, Provinssirock and world's oldest tango festival Tangomarkkinat are both held in Seinäjoki. External links. - Official site.
0.0282


Southern Ostrobothnia (;) is one of the 20 regions of Finland. Seinäjoki is the regional centre and by far the largest city in the area. Historical 
0.0284


 of the 20 regions of Finland. Seinäjoki is the regional centre and by far the largest city in the area. Historical provinces. For History, Geography and Culture see: Ostrobothnia. 
0.0286


 One of the biggest Rock festivals in Finland, Provinssirock and world's oldest tango festival Tangomarkkinat are both held in Seinäjoki. External links. - Official site.
0.0288


 translator between 1988 and 1990. He then joined the BBC, originally working for them as a translator, then as a sub-editor

 Cahill, Saturday Night Live castmember. Stephen Colbert, television host. Martin de Maat, teacher. Paul Dinello, Strangers with Candy actor/director. Jennifer Estlin Law & Order actor. Jon Favreau, Swingers writer and 
0.037


 Saturday Night Live castmember. Stephen Colbert, television host. Martin de Maat, teacher. Paul Dinello, Strangers with Candy actor/director. Jennifer Estlin Law & Order actor. Jon Favreau, Swingers writer and actor. Kate 
0.0372


 he was commissioned colonel. He later resigned due to ill health. Charles E. Stuart died in Kalamazoo and was interred in Mountain Home Cemetery. His home in Kalamazoo at 427 
0.0374


 from the state of Michigan. Biography. Stuart was born in New York, either near Waterloo, New York, or in Columbia County. He studied law, was admitted to the bar 
0.0376


 about the U.S. Representative and Senator from Michigan. For the claimant to the thrones of England, Scotland and Ireland, see Charles Edward Stuart. Charles Edward Stuart (Novem

...

 är sannerligen uppstånden!. Italic languages. Latin - Christus resurrexit! Resurrexit vere!. Romance languages. Aromanian - Hristolu unghia! Daleehira unghia!. Catalan - Crist ha ressuscitat! Veritablement ha ressuscitat!. French - Christ est 
0.958


 languages. Central Semitic languages. Aramaic languages. Syriac - ! ܡܫܝܚܐ ܩܡ! ܫܪܝܪܐܝܬ ܩܡ (Mshiḥa qām! sharīrāīth qām!; Mshiḥo Qom! Shariroith Qom). Neo-Syriac - ! ܡܫܝܚܐ ܩܡܠܗ! ܒܗܩܘܬܐ ܩܡܠܗ 
0.9582


 National Park (Parque Nacional do Itatiaia), established in 1937, is the oldest national park in Brazil. It is located on the border between Rio de Janeiro and Minas Gerais states, between 
0.9584


 Nacional do Itatiaia), established in 1937, is the oldest national park in Brazil. It is located on the border between Rio de Janeiro and Minas Gerais states, between 22º16’ - 
0.9586


 third highest mountain, Pico das Agulhas Negras, which stands at 2,878 meters. This peak is visible to the northwest of Resende when driving between São Paulo an

 Barnet, London, England. They currently play in the Isthmian League Premier Division. In the 2003-04 season they finished fourth in the Isthmian League Premier Division. However, they declined the automatic place 
0.9674


 Plastics factory due to initial media reports using this name - see detailed explanation below), in the Woodside district of Glasgow in western Scotland, exploded, killing nine people, including 
0.9676


On May 11, 2004, the ICL Plastics factory (Commonly referred to as Stockline Plastics factory due to 
0.9678


 factory (Commonly referred to as Stockline Plastics factory due to initial media reports using this name - see detailed explanation below), in the Woodside district of Glasgow in western Scotland, 
0.968


 of Mr. Smith's body from the site on May 14, Strathclyde Fire Brigade announced that they believed no hope of recovering live victims remained. Cause. The cause of the explosion was 
0.9682


 They categorized all leadership styles into five behavior 

Free energy suppression is a conspiracy theory that 
0.9762


 claims that advanced technology that would reshape current electrical generation methods is being suppressed by special interest groups. These groups are usually related to the oil industry, to whom current energy 
0.9764


 cost exist but are being suppressed by governments and special interest groups (such as the fossil fuel and nuclear industry), and that suppression has been going on for 
0.9766


 wealthy elites governments, deluded inventors and con men, as well as a non-demanding public. Historic cases. Many inventors have attempted to construct means of "over-unity" or perpetual motion energy 
0.9768


 and furnishing New Wardour Castle, designed in the Palladian style by Giacomo Quarenghi. After his death, his trustees were forced to sell off a portion of his lands in Dorset. See 
0.977


 of the Commonwealth of Pennsylvania from 1819 to 1820, and as the ninth Secretary of the U.S. Treasury from March 6, 1829 to Ju

 the fusion triple product achieved. ). JT-60 is a typical Tokamak with a D-shaped poloidal cross-section, similar to JET. Experimental results obtained by the reactor will no doubt be of 
0.9852


 for Japan Torus) is the flagship of Japan's magnetic fusion program, previously run by the Japan Atomic Energy Research Institute (JAERI) and currently run by the Japan 
0.9854


 Japan. In operation since 1985, it currently holds the record for the highest value of the fusion triple product achieved. ). JT-60 is a typical Tokamak with 
0.9856


 and structures. Historical revisionism. Fomenko is a supporter of drastically revising chronological history. He has created his own revision called New Chronology, based on statistical correlations, dating of zodiacs, 
0.9858


 (26 meters) to examine the stars Tau Ceti and Epsilon Eridani near the 1.420 gigahertz marker frequency. Both are nearby Sun-like stars that then seemed reasonably likely to have 
0.986


Project Ozma was a pioneering SETI

 Liverpool and Irish football teams of the 1980s; he has since become a radio, television and internet pundit for the BBC and Today FM. Despite being born in England
0.9942


 Kung Fu Records. An independent music video starring guitarist/producer Warren Fitzgerald was filmed for the song "Don't Stop Me Now," which is a cover of a song by the English rock band 
0.9944


 rock band Queen. The album's title is a reference to a vulgar Hollywood term for dried semen on a casting couch. Much of the album is characterized 
0.9946


 was settled with redesigned lettering which appears on all subsequent pressings of the album. Track listing. Performers. Dave Quackenbush - vocals. Warren Fitzgerald - guitar, backing vocals. Joe Escalante 
0.9948


 and was sent back with some of the collection on the Castle Forbes. The specimens were lost when the ship was wrecked off the Cape of Good Hope in July 1824. With 
0.995


Prosper Garnot (January 13, 1794 – 1838) was a French surgeon and naturalist. 

In [72]:
print(len(test_data_rnn))
print(len(lost_rnn))

809
4950


### Save training and test data

In [74]:

# Store data (serialize)
with open('training_data_rnn_{}.pickle'.format(str(len(training_data_rnn))), 'wb') as handle:
    pickle.dump(training_data_rnn, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('test_data_rnn_{}.pickle'.format(str(len(test_data_rnn))), 'wb') as handle:
    pickle.dump(test_data_rnn, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [62]:
test(test_data_rnn, RNN_with_attention)

KeyError: 'types'

In [69]:
test_data_rnn[0]['graph'].keys()

dict_keys(['vectors'])